In [1]:
!pip install aiofiles tqdm

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.2.1 -> 23.3.1
[notice] To update, run: pip install --upgrade pip


In [2]:
import asyncio
import json
import os
import re

import aiofiles
import aiohttp
import pandas as pd
import requests
import tqdm.asyncio

from restgdf.utils.crawl import fetch_all_data
from restgdf.utils.getinfo import service_metadata, get_metadata


api_root = "http://restgdf_api:8080"
ms_root = f"{api_root}/mappingsupport"
ms_endpoints = {name: f"{ms_root}/{name}" for name in ('state', 'county', 'town')} | {"root": f"{api_root}/mappingsupport"}


def get_df() -> pd.DataFrame:
    resp = requests.get(ms_endpoints['root'])
    data = resp.json()
    return pd.DataFrame(data)


def get_unique_roots(df: pd.DataFrame) -> pd.Series:
    pat = re.compile(r"(?P<root>^.*/rest/services?).*?$", re.IGNORECASE)
    return (
        df
        .join(
            df['ArcGIS-url']
            .dropna()
            .str.strip()
            .str.extract(pat)
            ['root']
            .dropna()
        )
        ['root']
        .dropna()
        .drop_duplicates()
        .sort_values()
    )


In [3]:
%%time

df = get_df()

unique_roots = get_unique_roots(df)

CPU times: user 34.2 ms, sys: 3.42 ms, total: 37.6 ms
Wall time: 241 ms


In [4]:
unique_root_hashes = pd.util.hash_pandas_object(unique_roots)

unique_root_df = pd.DataFrame(zip(unique_roots, unique_root_hashes), columns=['url','hash'])

unique_root_df.head()

url                  hash
0         http://136.234.13.165/arcgis/rest/services   8489457957960488436
1      http://216.167.160.20/arcgis107/rest/services   4291004727045614516
2  http://ags.co.okaloosa.fl.us/arcgis/rest/services  10213391155691883489
3     http://arcgis.dcnr.nv.gov/arcgis/rest/services   8177309747274201625
4  http://arcgis2.williamsoncounty-tn.gov/arcgis/...   1860738680214392857

In [5]:
unique_root_df.to_csv('unique_roots.csv', index=False)

In [6]:
done_dict = {(r.url, r.hash): False for r in unique_root_df.itertuples(index=False)}

In [7]:
async def scrape_to_files(url_hash_dict: dict[tuple, bool], output_directory: str) -> dict[tuple, bool]:
    done_dict = url_hash_dict
    async with aiohttp.ClientSession(connector=aiohttp.TCPConnector(ssl=False)) as session:

        async def fetch_to_file(url: str, hash: int) -> None:
            filepath = os.path.join(output_directory, f"{hash}.json")
            if os.path.exists(filepath):
                return None
            try:
                data = await fetch_all_data(session, url, return_feature_count=False)
                if 'error' in data:
                    data['error'] = str(data['error'])
                async with aiofiles.open(filepath, 'w') as outf:
                    await outf.write(json.dumps(data))
                done_dict[(url, hash)] = True
            except Exception as e:
                done_dict[(url, hash)] = e
        
        tasks = [fetch_to_file(url, hash) for url, hash in done_dict.keys()]
        results = await tqdm.asyncio.tqdm_asyncio.gather(*tasks)
        return done_dict


In [8]:
output_dir = os.path.abspath("output")

if not os.path.exists(output_dir):
    os.mkdir(output_dir)

In [9]:
import nest_asyncio

nest_asyncio.apply()

In [10]:
%%time

results = asyncio.run(scrape_to_files(done_dict, output_dir))

100%|██████████| 2038/2038 [24:38<00:00,  1.38it/s] 

CPU times: user 21min 43s, sys: 35.1 s, total: 22min 18s
Wall time: 24min 38s
